# 2D Electrodynamics with FEM - Exterior Finite Elements

or rather Magnetostatics in 2D

In [ ]:
try:
    import ngsolve
except ImportError:
    !wget "https://fem-on-colab.github.io/releases/ngsolve-install.sh" -O "/tmp/ngsolve-install.sh" && bash "/tmp/ngsolve-install.sh"
    import ngsolve

In [ ]:
from ngsolve import *
#from ngsolve.meshes import *
from ngsolve.solvers import *
from ngsolve.webgui import Draw
from netgen.geom2d import unit_square

#import matplotlib.pyplot as plt
#import numpy as np

import time
import json


Setting some parameters in the simulation
including the folders name for saving results

In [ ]:
parameters = {}
#parameters["h"] = 0.025
#parameters["h"] = 0.05
#parameters["n"] = int(1/parameters["h"])
parameters["n"] = 20
parameters["h"] = 1./parameters["n"]
parameters["order"] = 1
parameters["CFJ"] = 1000*CF((0.,x*(1-x)))

Mesh generation with periodic boundary conditions

In [ ]:
ne=parameters["n"]
h=parameters["h"]
#mesh = MakeStructured2DMesh(quads=False, nx=ne, ny=ne, periodic_x=True, periodic_y=True)
#mesh = MakeStructured2DMesh(quads=True, nx=ne, ny=ne, periodic_x=True, periodic_y=True)
#mesh = MakeStructured2DMesh(quads=False, nx=ne, ny=ne, periodic_x=False, periodic_y=False)

mesh = Mesh(unit_square.GenerateMesh(maxh=h))

Draw(mesh)

## de-Rham chain in 2D

with $k$-forms $\omega \in \Lambda^k(M;\mathbb{R})$ and $k \le 2$:

$\Lambda^0(M;\mathbb{R}) \stackrel{\mathrm{d}_0}{\rightarrow} \Lambda^1(M;\mathbb{R}) \stackrel{\mathrm{d}_1}{\rightarrow} \Lambda^2(M;\mathbb{R}) $

interpreted as vector fields using

* weak differentiability (Sobolev spaces)
* musical isomorphism  $TM^* \stackrel{\sharp}{\rightarrow} TM$ ( $\simeq$ "raising and lowering of indices" using metric)

$H^1(M;\mathbb{R}) \stackrel{\mathrm{grad}}{\rightarrow} Hcurl(M;\mathbb{R}) \stackrel{\mathrm{curl}}{\rightarrow} Hdiv(M;\mathbb{R}) $


## Finite Element Spaces

Exterior Finite Elements
* $A \in \Lambda^1_h(M;\mathbb{R}) \subset Hcurl(M;\mathbb{R})$
* $J \in \Lambda^1_h(M;\mathbb{R}) \subset Hcurl(M;\mathbb{R})$
* $F \in \Lambda^2_h(M;\mathbb{R}) \subset Hdiv(M;\mathbb{R})$


In [ ]:
order=parameters["order"]
fesA = HCurl(mesh, order=order)
fesF = L2(mesh, order=order-1)
fesf = H1(mesh, order=order+1)

def draw_basis_loop(fes, draw_kwargs={}):
    #print(fes)
    mesh = fes.mesh
    gfviz = GridFunction(fes)
    gfviz.vec.data[:] = 0.
    scene = Draw(gfviz, mesh, **draw_kwargs)

    for dof_i in range(len(gfviz.vec)):
        gfviz.vec.data[:] = 0.
        gfviz.vec.data[dof_i] = 1.
        #print(dir(scene))
        scene.Redraw()
        #print ('r', f"fes basis function nr {dof_i}", end="")
        time.sleep(1)

    return scene

def draw_basis_k_loop(fes, dof_i, draw_kwargs={}):
    #print(fes)
    mesh = fes.mesh
    gfviz = GridFunction(fes)
    gfviz.vec.data[:] = 0.
    gfviz.vec.data[dof_i] = 1.
    scene = Draw(gfviz, mesh, **draw_kwargs)

    return scene

#scene = draw_basis_loop(fesA)
dof_i = int(mesh.nv/2) + int(sqrt(mesh.nv))
scene = draw_basis_k_loop(fesf, dof_i)
#dof_i = int(mesh.nedge/2) + int(sqrt(mesh.nedge))
#scene = draw_basis_k_loop(fesA, dof_i, draw_kwargs={"vectors": True})
#dof_i = int(mesh.ne/2) + int(sqrt(mesh.ne))
#scene = draw_basis_k_loop(fesF, dof_i)

#print(dir(scene))

#draw_basis_loop(fesf)
#draw_basis_loop(fesA, draw_kwargs={"vectors": True})
#draw_basis_loop(fesF)

## Maxwell's Equations

* Given $J \in \Lambda^1(M;\mathbb{R})$
* Find $A \in \Lambda^1(M;\mathbb{R})$:

\begin{align*}
    &\int_M \langle F(A), \mathrm{d} A^\prime \rangle = \int_M \langle J, A^\prime \rangle \quad \forall A^\prime \in \Lambda^1(M;\mathbb{R}) \\
    &\int_M \langle \mathrm{d} A, \mathrm{d} A^\prime \rangle = \int_M \langle J, A^\prime \rangle \quad \forall A^\prime \in \Lambda^1(M;\mathbb{R})
\end{align*}

## Discrete Maxwell's Equations

* Given $J_h \in \Lambda^1_h(M;\mathbb{R})$
* Find $A_h \in \Lambda^1_h(M;\mathbb{R})$:

\begin{align*}
    &\int_M \langle F(A_h), \mathrm{d} A^\prime_h \rangle = \int_M \langle J_h, A^\prime_h \rangle \quad \forall A^\prime_h \in \Lambda^1_h(M;\mathbb{R}) \\
    &\int_M \langle \mathrm{d} A_h, \mathrm{d} A^\prime_h \rangle = \int_M \langle J_h, A^\prime_h \rangle \quad \forall A^\prime_h \in \Lambda^1_h(M;\mathbb{R})
\end{align*}

## Matrix Assembly

Creating symbolic TrialFunction and TestFunction for assembly of bilinear forms

* Whitney $1$-forms $\lambda_L$
* Mass Matrix $M_{L L^\prime} = \int_M \langle \lambda_L , \lambda_{L^\prime} \rangle$
* Stiffness Matrix $ D_{L L^\prime} = -\int_M \langle \mathrm{d} \lambda_L , \mathrm{d} \lambda_{L^\prime} \rangle $

In [ ]:
# TrialFunction = the unknown in the equation
A = fesA.TrialFunction()
# TestFunction = the variational direction in the equation
Ap = fesA.TestFunction()

# Create symbolic Bilinear forms
M = BilinearForm(fesA)
D = BilinearForm(fesA)
# at the moment "empty"...

# add the terms:
M += InnerProduct(A,Ap)*dx
D += -InnerProduct(curl(A),curl(Ap))*dx


# regularization needed ...
# (... or a gauge - later)
eps = 0.0000001
D += -eps*InnerProduct(A,Ap)*dx
# at the moment the matrices are defined purely symbolically according to a calculation "recipe"

# Assemble the matrices by a manual function call
M.Assemble()
D.Assemble()

## Linear Form Assembly

In practice current $J \in \Lambda^1(M;\mathbb{R})$ is provided in the Bilinear form $ \int_M \langle J, A^\prime \rangle$

it therefore is a linear form with fixed $J \in \Lambda^1(M;\mathbb{R})$ and argument $A^\prime \in \Lambda^1(M;\mathbb{R})$

Or in the discrete case:

* Linear form $ \int_M \langle J_h, A^\prime_h \rangle$
* fixed (interpolated) $I_h^1 J =  J_h \in \Lambda^1_h(M;\mathbb{R})$
* argument $A^\prime_h \in \Lambda^1_h(M;\mathbb{R})$

In [ ]:
# GridFunctions are discrete functions
# represented by a vector of coefficients
# in the Basis of Whitney $k$-forms
gfJ = GridFunction(fesA)

# symbolically define the current CoefficientFunction
CFJ = parameters["CFJ"]

# Set the current value
# by interpolating a (symbolically provided) CoefficientFunction
gfJ.Set( CFJ )

# Creat symbolic Linear form
J = LinearForm(fesA)
# at the moment "empty" ...

# add the terms:
J += InnerProduct(gfJ,Ap)*dx
# at the moment the matrices are defined purely symbolically according to a calculation "recipe"

# Assemble the matrices by a manual function call
J.Assemble()

Draw(gfJ, mesh, vectors=True)

## Solving the Discrete Equation

Invert the stiffness matrix and multiply with the linear form

$D \vec{A} = \vec{J}^\top$

$\vec{A} = D^{-1} \vec{J}^\top$

In [ ]:
gfA = GridFunction(fesA)

# Invert the stiffness matrix
Dinv = D.mat.Inverse(fesA.FreeDofs(), inverse="umfpack")
#Dinv = D.mat.Inverse(fesA.FreeDofs(), inverse="sparsecholesky")

# Solve the equation
gfA.vec.data = Dinv * J.vec

## Coulomb Gauge

enforce additional constraint:

\begin{align*}
\mathrm{div} A = 0
\end{align*}

or in weak form

\begin{align*}
    \int_M \langle A, \mathrm{d} f^\prime \rangle = 0 \quad \forall f^\prime \in \Lambda^0(M;\mathbb{R}) \\
\end{align*}

## Maxwell's Equations with Coulomb Gauge - Mixed Formulation

* Given $J \in \Lambda^1(M;\mathbb{R})$
* Find $A \in \Lambda^1(M;\mathbb{R})$
*  Find $f \in \Lambda^0(M;\mathbb{R})$

\begin{align*}
    &\int_M \langle \mathrm{d} A, \mathrm{d} A^\prime \rangle &+& \int_M \langle \mathrm{d} f, A^\prime \rangle &=& \int_M \langle J, A^\prime \rangle &\quad \forall A^\prime \in \Lambda^1(M;\mathbb{R}) \\
    &\int_M \langle A, \mathrm{d} f^\prime \rangle &+& 0   &=& 0 &\quad \forall f^\prime \in \Lambda^0(M;\mathbb{R}) \\
\end{align*}

In [ ]:
fesA = HCurl(mesh,order=order)
fesf = H1(mesh,order=order+1)

# in reality, the lagrange multiplie is not unique
# this woudl fix an additional constraint
# the code below still works without it ...
#fesN = NumberSpace(mesh)

fesAf = fesA*fesf
#fesAf = fesA*fesf*fesN

A, f = fesAf.TrialFunction()
Ap, fp = fesAf.TestFunction()

# A, f, C = fesAf.TrialFunction()
# Ap, fp, Cp = fesAf.TestFunction()

Df = BilinearForm(fesAf, symmetric=True)

Df += InnerProduct(curl(A),curl(Ap))*dx

Df += InnerProduct(grad(f),Ap)*dx
Df += InnerProduct(A,grad(fp))*dx

#Df += InnerProduct(f,Cp)*dx
#Df += InnerProduct(C,fp)*dx


Df.Assemble()

Dfinv = Df.mat.Inverse(fesAf.FreeDofs(), inverse="umfpack")
#Dfinv = Df.mat.Inverse(fesAf.FreeDofs(), inverse="sparsecholesky")
#Dfinv = Df.mat.Inverse(fesAf.FreeDofs(), inverse="pardiso")

#eps = 0.00001
#eps = 1
#Df += eps*InnerProduct(A,Ap)*dx
#Df += eps*InnerProduct(f,fp)*dx
#Df += eps*InnerProduct(C,Cp)*dx


Jf = LinearForm(fesAf)
gfJf = GridFunction(fesAf)
gfJ = gfJf.components[0]
CFJ = parameters["CFJ"]
gfJ.Set( CFJ )
Jf += InnerProduct(gfJ,Ap)*dx

Jf.Assemble()


gfAf = GridFunction(fesAf)

gfAf.vec.data[:] = Dfinv * Jf.vec

gfA = gfAf.components[0]
gff = gfAf.components[1]
#Draw(gfJ, mesh, vectors=True)
Draw(gfA, mesh, vectors=True)

Evaluating the field strength $F(A)$
by solving the equation $F(A) = \mathrm{d} A$ in weak form

\begin{align*}
    \int_M \langle F(A), F^\prime \rangle = \int_M \langle \mathrm{d} A, F^\prime \rangle \quad \forall F^\prime \in \Lambda^2(M;\mathbb{R})
\end{align*}

discrete form:

\begin{align*}
    \int_M \langle F(A_h), F^\prime_h \rangle = \int_M \langle \mathrm{d} A_h, F^\prime_h \rangle \quad \forall F^\prime_h \in \Lambda^2_h(M;\mathbb{R})
\end{align*}

\begin{align*}
    M_F \vec{F} = \vec{C}^\top
\end{align*}

In [ ]:
fesF = L2(mesh, order=order-1)
F = fesF.TrialFunction()
Fp = fesF.TestFunction()

MF = BilinearForm(fesF)
CA = LinearForm(fesF)

MF += InnerProduct(F,Fp)*dx
CA += InnerProduct(curl(gfA),Fp)*dx

MF.Assemble()
CA.Assemble()

MFinv = MF.mat.Inverse(fesF.FreeDofs(), inverse="sparsecholesky")

gfF = GridFunction(fesF)

gfF.vec.data = MFinv * CA.vec

#gfF.Set(curl(gfA))
#cfF = curl(gfAf.components[0])

## Inspect the solution

In [ ]:
Jscene = Draw(gfJ, mesh, vectors=True)

In [ ]:
Ascene = Draw(gfA, mesh, vectors=True)

In [ ]:
Fscene = Draw(gfF, mesh)
#Fscene = Draw(cfF, mesh)